Clusters to Skill names

In [1]:
import os
import pandas as pd
import numpy as np
import sys
import re
import json

import csv
import time
from datetime import date, datetime

from dotenv import load_dotenv
from openai import AzureOpenAI

from langchain_openai import AzureChatOpenAI
from langchain.schema import HumanMessage

print(date.today())
print('Python version:', sys.version)
print('\nWorking directory:', os.getcwd())
os.chdir(r'C:\Users\Denis_Davydov2\OneDrive - EPAM\Prophet_AI_docs\Datasets\AI_skills\Topics')
print('\nCurrent working directory:', os.getcwd())
print("Last run:", date.today())

2025-11-13
Python version: 3.13.5 | packaged by Anaconda, Inc. | (main, Jun 12 2025, 16:37:03) [MSC v.1929 64 bit (AMD64)]

Working directory: c:\Users\Denis_Davydov2\OneDrive\Scipts\Py_Scripts\EPAM\Prophet\AI_skills\Ver_2

Current working directory: C:\Users\Denis_Davydov2\OneDrive - EPAM\Prophet_AI_docs\Datasets\AI_skills\Topics
Last run: 2025-11-13


# Get data

In [8]:
# Load clustering results

file_path = 'C:\\Users\\Denis_Davydov2\\OneDrive - EPAM\\Prophet_AI_docs\\Datasets\\AI_skills\\Clusters\\'
file_name = 'cluster_k50_r8.0_selftuned_clusters.csv'

clusters = pd.read_csv(file_path+file_name)
print("File read: ", file_name)

clusters

File read:  cluster_k50_r8.0_selftuned_clusters.csv


cluster_id  cluster_size  avg_distance  std_distance  min_distance  \
0             0           123        0.4369        0.1003        0.0074   
1             1           117        0.6215        0.1497        0.0369   
2             2           106        0.6026        0.1492        0.0156   
3             6            98        0.5829        0.1401        0.0489   
4             7            96        0.5201        0.1950        0.0121   
..          ...           ...           ...           ...           ...   
139         136            12        0.2578        0.1945        0.0216   
140         135            12        0.2344        0.1601        0.0384   
141         141            11        0.4085        0.1703        0.0446   
142         137             9        0.4127        0.1361        0.0246   
143         138             9        0.2105        0.1068        0.0522   

     max_distance  avg_dist_to_center                                centroid  \
0          0.7597              0.2472                               llm usage   
1          1.1895              0.3805               amazon web services (aws)   
2          1.1144              0.3651                                   agent   
3          1.1817              0.3496                           data handling   
4          1.0739              0.3034                      8-bit quantization   
..            ...                 ...                                     ...   
139        0.7389              0.1261            mcp (model control protocol)   
140        0.6244              0.1139                     no-code development   
141        0.8095              0.2071                      ai risk management   
142        0.6465              0.2043  gans (generative adversarial networks)   
143        0.4409              0.0984                    serverless computing   

                                     closest_5_members  \
0    ['llm usage', 'llm application', 'llm applicat...   
1    ['amazon web services (aws)', 'amazon ebs', 'a...   
2    ['agent', 'agent-to-agent communication', 'age...   
3    ['data handling', 'dataset management', 'datas...   
4    ['8-bit quantization', 'int8 quantization', 'q...   
..                                                 ...   
139  ['mcp (model control protocol)', 'model contex...   
140  ['no-code development', 'no-code ai developmen...   
141  ['ai risk management', 'risk management', 'ris...   
142  ['gans (generative adversarial networks)', 'ge...   
143  ['serverless computing', 'serverless ai', 'ser...   

                                               members  \
0    ['llm usage', 'llm application', 'llm applicat...   
1    ['amazon web services (aws)', 'amazon ebs', 'a...   
2    ['agent', 'agent-to-agent communication', 'age...   
3    ['data handling', 'dataset management', 'datas...   
4    ['8-bit quantization', 'int8 quantization', 'q...   
..                                                 ...   
139  ['mcp (model control protocol)', 'model contex...   
140  ['no-code development', 'no-code ai developmen...   
141  ['ai risk management', 'risk management', 'ris...   
142  ['gans (generative adversarial networks)', 'ge...   
143  ['serverless computing', 'serverless ai', 'ser...   

                                       members_cleaned  cleaned_size  
0    ['audio llms', 'code generation (llms)', 'code...           123  
1    ['alexa', 'alexa integration', 'alexa skill de...           115  
2    ['a2a protocol', 'action', 'action agent', 'ag...           105  
3    ['ai data management', 'data acquisition', 'da...            97  
4    ['1-bit inference', '1-bit llm', '1-bit quanti...            96  
..                                                 ...           ...  
139  ['mcp (model context protocol)', 'mcp (model c...            12  
140  ['design-to-code', 'low-code ai', 'low-code de...            12  
141  ['ai risk assessment', 'ai risk management', '...            11  
142  ['conditional gan', 'c

# Namind

In [9]:
# === Load Environment Variables ===
load_dotenv()  # Loads variables from .env file into environment

# Retrieve database connection parameters from environment variables
DIAL_API_KEY = os.getenv('DIAL_API_KEY')

#print(DIAL_API_KEY)

In [14]:
prompt = f"""To which AI-related skill do all of the following terms belong? 
Give this hard skill a short name and provide a brief description.

OUTPUT MUST BE ONLY JSON (enforced separately). DO NOT include explanations here.

Schema (each object):
  skill_name  -> concise, specific category name (2-5 words, no internal quotes)
  department  -> functional area and a short definition in 1-2 sentences

Cluster composition (terms):
{terms}
"""

print(prompt)

To which AI-related skill do all of the following terms belong? 
Give this hard skill a short name and provide a brief description.

OUTPUT MUST BE ONLY JSON (enforced separately). DO NOT include explanations here.

Schema (each object):
  skill_name  -> concise, specific category name (2-5 words, no internal quotes)
  department  -> functional area and a short definition in 1-2 sentences

Cluster composition (terms):
["['audio llms', 'code generation (llms)', 'code generation with llms', 'code llms', 'codellm', 'coding with llms', 'cost optimization for llms', 'custom llm', 'efficient llm training', 'fine-tuning (llm)', 'fine-tuning llms', 'google llms', 'grounded llms', 'large language model (llm)', 'large language model (llm) training', 'large language model optimization (llmo)', 'litellm', 'llm (large language model)', 'llm agent framework', 'llm agents', 'llm alignment', 'llm api', 'llm api integration', 'llm application', 'llm application development', 'llm architecture', 'llm ar

In [15]:
import ast
import json
import re
from typing import List, Dict, Any
from datetime import datetime

# === Guards ===
if 'clusters' not in globals():
    raise RuntimeError("'clusters' DataFrame not found. Run the data loading cell before this one.")
if 'DIAL_API_KEY' not in globals() or not DIAL_API_KEY:
    raise RuntimeError("DIAL_API_KEY missing. Ensure .env is loaded.")

# === Azure OpenAI Model Init (reuse if already created) ===
try:
    model  # type: ignore
except NameError:
    model = AzureChatOpenAI(
        azure_endpoint="https://ai-proxy.lab.epam.com",
        api_key=DIAL_API_KEY,
        api_version="2025-04-01-preview",
        model='gpt-5-2025-08-07'
    )

# === System Instructions ===
system_instructions = (
    "You are an expert in talent acquisition and employee training for AI development and implementation teams. "
    "Goal: Given a list of AI-related terms that co-occur in one cluster, produce a concise hard skill name and a brief definition that would be useful for recruitment and workforce development. "
    "Return ONLY a valid JSON object (UTF-8) with exactly these keys: \n"
    "{\n  \"skill_name\": \"string\",  \n  \"skill_definition\": \"string\" \n}\n"
    "Constraints: \n"
    "- skill_name: 2-5 words, no quotes inside, no trailing punctuation.\n"
    "- skill_definition: 1-2 sentences, actionable, describes practical capability.\n"
    "- Use only double quotes, no comments, no markdown, no code fences. Output MUST start with '{' and end with '}'."
)

# === Helpers ===
TERM_SPLIT_RE = re.compile(r'[;,]|\t|\n')

def parse_terms(raw: Any) -> List[str]:
    """Parse the 'members_cleaned' field into a list of distinct, cleaned terms."""
    if raw is None:
        return []
    if isinstance(raw, list):
        base = raw
    else:
        text = str(raw).strip()
        # Try JSON or literal list first
        if (text.startswith('[') and text.endswith(']')) or (text.startswith('(') and text.endswith(')')):
            try:
                maybe = ast.literal_eval(text)
                if isinstance(maybe, (list, tuple)):
                    base = list(maybe)
                else:
                    base = [text]
            except Exception:
                base = TERM_SPLIT_RE.split(text)
        else:
            base = TERM_SPLIT_RE.split(text)
    cleaned = []
    for t in base:
        t2 = re.sub(r'\s+', ' ', str(t)).strip().strip('"').strip("'")
        if t2:
            cleaned.append(t2)
    # Deduplicate preserving order
    seen = set()
    uniq = []
    for t in cleaned:
        if t.lower() not in seen:
            seen.add(t.lower())
            uniq.append(t)
    return uniq

def build_user_prompt(terms: List[str]) -> str:
    sample = ', '.join(terms[:40])  # cap terms for token efficiency
    return (
        "Terms in cluster:\n" + sample + "\n\n" +
        "Produce JSON now."  # Reinforce immediate JSON output
    )

def extract_json_object(text: str) -> str:
    text = text.strip()
    # Remove code fences if present
    if text.startswith('```'):
        parts = text.split('```')
        if len(parts) > 1:
            text = parts[1].strip()
    start = text.find('{')
    end = text.rfind('}')
    if start != -1 and end != -1 and end > start:
        return text[start:end+1]
    raise ValueError('Could not locate JSON object boundaries.')

def call_model(terms: List[str], max_retries: int = 2) -> Dict[str, str]:
    user_prompt = build_user_prompt(terms)
    messages = [
        ("system", system_instructions),
        ("human", user_prompt)
    ]
    last_err = None
    for attempt in range(1, max_retries + 2):
        try:
            out = model.invoke(messages)
            raw = out.content.strip()
            js = extract_json_object(raw)
            data = json.loads(js)
            # Basic validation
            if not isinstance(data, dict):
                raise ValueError('JSON root not an object')
            skill_name = data.get('skill_name') or data.get('group_name')  # fallback if model used group_name
            skill_def = data.get('skill_definition') or data.get('department')
            if not skill_name or not skill_def:
                raise ValueError('Missing required keys in JSON')
            return {
                'skill_name': str(skill_name).strip(),
                'skill_definition': str(skill_def).strip()
            }
        except Exception as e:  # noqa: BLE001
            last_err = e
            print(f"Attempt {attempt} failed: {e}")
    print("All attempts failed; returning placeholders.")
    return {
        'skill_name': 'Unclassified Skill',
        'skill_definition': f'Failed to generate definition: {last_err}'
    }

# === Main Processing Loop ===
start_ts = datetime.now()
print(f"Starting skill naming at {start_ts}")

# Initialize / Preserve existing columns to allow re-run without overwriting successful rows
if 'skill_name' not in clusters.columns:
    clusters['skill_name'] = None
if 'skill_definition' not in clusters.columns:
    clusters['skill_definition'] = None

rows_total = len(clusters)
for idx, row in clusters.iterrows():
    # Skip already processed rows to allow safe reruns
    if pd.notnull(row.get('skill_name')) and pd.notnull(row.get('skill_definition')):
        continue
    terms = parse_terms(row.get('members_cleaned'))
    if not terms:
        clusters.at[idx, 'skill_name'] = 'Empty Cluster'
        clusters.at[idx, 'skill_definition'] = 'No terms available to describe.'
        continue
    result = call_model(terms)
    clusters.at[idx, 'skill_name'] = result['skill_name']
    clusters.at[idx, 'skill_definition'] = result['skill_definition']

    if (idx + 1) % 10 == 0 or (idx + 1) == rows_total:
        print(f"Processed {idx + 1}/{rows_total} rows.")

end_ts = datetime.now()
print(f"Completed at {end_ts}. Duration: {end_ts - start_ts}")

# Preview
clusters[['members_cleaned', 'skill_name', 'skill_definition']].head()

Starting skill naming at 2025-11-12 18:32:13.061372
Processed 10/144 rows.
Processed 10/144 rows.
Processed 20/144 rows.
Processed 20/144 rows.
Processed 30/144 rows.
Processed 30/144 rows.
Processed 40/144 rows.
Processed 40/144 rows.
Processed 50/144 rows.
Processed 50/144 rows.
Processed 60/144 rows.
Processed 60/144 rows.
Processed 70/144 rows.
Processed 70/144 rows.
Processed 80/144 rows.
Processed 80/144 rows.
Processed 90/144 rows.
Processed 90/144 rows.
Processed 100/144 rows.
Processed 100/144 rows.
Processed 110/144 rows.
Processed 110/144 rows.
Processed 120/144 rows.
Processed 120/144 rows.
Processed 130/144 rows.
Processed 130/144 rows.
Processed 140/144 rows.
Processed 140/144 rows.
Processed 144/144 rows.
Completed at 2025-11-12 19:02:37.522924. Duration: 0:30:24.461552
Processed 144/144 rows.
Completed at 2025-11-12 19:02:37.522924. Duration: 0:30:24.461552


members_cleaned  \
0  ['audio llms', 'code generation (llms)', 'code...   
1  ['alexa', 'alexa integration', 'alexa skill de...   
2  ['a2a protocol', 'action', 'action agent', 'ag...   
3  ['ai data management', 'data acquisition', 'da...   
4  ['1-bit inference', '1-bit llm', '1-bit quanti...   

                               skill_name  \
0             LLM Application Engineering   
1               Alexa and AWS Development   
2                    AI Agent Engineering   
3                     AI Data Engineering   
4  Model Quantization and Mixed Precision   

                                    skill_definition  
0  Design, build, and deploy LLM-powered applicat...  
1  Design, build, and deploy Alexa skills and voi...  
2  Design, program, and deploy autonomous AI agen...  
3  Ability to design, build, and manage scalable ...  
4  Ability to design, implement, and optimize low...

In [16]:
clusters

cluster_id  cluster_size  avg_distance  std_distance  min_distance  \
0             0           123        0.4369        0.1003        0.0074   
1             1           117        0.6215        0.1497        0.0369   
2             2           106        0.6026        0.1492        0.0156   
3             6            98        0.5829        0.1401        0.0489   
4             7            96        0.5201        0.1950        0.0121   
..          ...           ...           ...           ...           ...   
139         136            12        0.2578        0.1945        0.0216   
140         135            12        0.2344        0.1601        0.0384   
141         141            11        0.4085        0.1703        0.0446   
142         137             9        0.4127        0.1361        0.0246   
143         138             9        0.2105        0.1068        0.0522   

     max_distance  avg_dist_to_center                                centroid  \
0          0.7597              0.2472                               llm usage   
1          1.1895              0.3805               amazon web services (aws)   
2          1.1144              0.3651                                   agent   
3          1.1817              0.3496                           data handling   
4          1.0739              0.3034                      8-bit quantization   
..            ...                 ...                                     ...   
139        0.7389              0.1261            mcp (model control protocol)   
140        0.6244              0.1139                     no-code development   
141        0.8095              0.2071                      ai risk management   
142        0.6465              0.2043  gans (generative adversarial networks)   
143        0.4409              0.0984                    serverless computing   

                                     closest_5_members  \
0    ['llm usage', 'llm application', 'llm applicat...   
1    ['amazon web services (aws)', 'amazon ebs', 'a...   
2    ['agent', 'agent-to-agent communication', 'age...   
3    ['data handling', 'dataset management', 'datas...   
4    ['8-bit quantization', 'int8 quantization', 'q...   
..                                                 ...   
139  ['mcp (model control protocol)', 'model contex...   
140  ['no-code development', 'no-code ai developmen...   
141  ['ai risk management', 'risk management', 'ris...   
142  ['gans (generative adversarial networks)', 'ge...   
143  ['serverless computing', 'serverless ai', 'ser...   

                                               members  \
0    ['llm usage', 'llm application', 'llm applicat...   
1    ['amazon web services (aws)', 'amazon ebs', 'a...   
2    ['agent', 'agent-to-agent communication', 'age...   
3    ['data handling', 'dataset management', 'datas...   
4    ['8-bit quantization', 'int8 quantization', 'q...   
..                                                 ...   
139  ['mcp (model control protocol)', 'model contex...   
140  ['no-code development', 'no-code ai developmen...   
141  ['ai risk management', 'risk management', 'ris...   
142  ['gans (generative adversarial networks)', 'ge...   
143  ['serverless computing', 'serverless ai', 'ser...   

                                       members_cleaned  cleaned_size  \
0    ['audio llms', 'code generation (llms)', 'code...           123   
1    ['alexa', 'alexa integration', 'alexa skill de...           115   
2    ['a2a protocol', 'action', 'action agent', 'ag...           105   
3    ['ai data management', 'data acquisition', 'da...            97   
4    ['1-bit inference', '1-bit llm', '1-bit quanti...            96   
..                                                 ...           ...   
139  ['mcp (model context protocol)', 'mcp (model c...            12   
140  ['design-to-code', 'low-code ai', 'low-code de...            12   
141  ['ai risk assessment', 'ai risk management', '...            11   
142  ['conditiona

# Save result

In [18]:
#Save result

file_path = 'C:\\Users\\Denis_Davydov2\\OneDrive - EPAM\\Prophet_AI_docs\\Datasets\\AI_skills\\Clusters\\'
file_name = f'Skills_with_names_{date.today()}.csv'

clusters.to_csv(file_path + file_name, index=False)
print(f"File {file_name} uploaded: ", date.today())
print(clusters.shape)




File Skills_with_names_2025-11-12.csv uploaded:  2025-11-12
(144, 14)


# Skills Embedding

## Get data

In [2]:
file_path = 'C:\\Users\\Denis_Davydov2\\OneDrive - EPAM\\Prophet_AI_docs\\Datasets\\AI_skills\\Clusters\\'
file_name = 'Skills_with_names_2025-11-12.csv'
skills = pd.read_csv(file_path+file_name)
print("File read: ", file_name)

skills

File read:  Skills_with_names_2025-11-12.csv


cluster_id  cluster_size  avg_distance  std_distance  min_distance  \
0             0           123        0.4369        0.1003        0.0074   
1             1           117        0.6215        0.1497        0.0369   
2             2           106        0.6026        0.1492        0.0156   
3             6            98        0.5829        0.1401        0.0489   
4             7            96        0.5201        0.1950        0.0121   
..          ...           ...           ...           ...           ...   
139         136            12        0.2578        0.1945        0.0216   
140         135            12        0.2344        0.1601        0.0384   
141         141            11        0.4085        0.1703        0.0446   
142         137             9        0.4127        0.1361        0.0246   
143         138             9        0.2105        0.1068        0.0522   

     max_distance  avg_dist_to_center                                centroid  \
0          0.7597              0.2472                               llm usage   
1          1.1895              0.3805               amazon web services (aws)   
2          1.1144              0.3651                                   agent   
3          1.1817              0.3496                           data handling   
4          1.0739              0.3034                      8-bit quantization   
..            ...                 ...                                     ...   
139        0.7389              0.1261            mcp (model control protocol)   
140        0.6244              0.1139                     no-code development   
141        0.8095              0.2071                      ai risk management   
142        0.6465              0.2043  gans (generative adversarial networks)   
143        0.4409              0.0984                    serverless computing   

                                     closest_5_members  \
0    ['llm usage', 'llm application', 'llm applicat...   
1    ['amazon web services (aws)', 'amazon ebs', 'a...   
2    ['agent', 'agent-to-agent communication', 'age...   
3    ['data handling', 'dataset management', 'datas...   
4    ['8-bit quantization', 'int8 quantization', 'q...   
..                                                 ...   
139  ['mcp (model control protocol)', 'model contex...   
140  ['no-code development', 'no-code ai developmen...   
141  ['ai risk management', 'risk management', 'ris...   
142  ['gans (generative adversarial networks)', 'ge...   
143  ['serverless computing', 'serverless ai', 'ser...   

                                               members  \
0    ['llm usage', 'llm application', 'llm applicat...   
1    ['amazon web services (aws)', 'amazon ebs', 'a...   
2    ['agent', 'agent-to-agent communication', 'age...   
3    ['data handling', 'dataset management', 'datas...   
4    ['8-bit quantization', 'int8 quantization', 'q...   
..                                                 ...   
139  ['mcp (model control protocol)', 'model contex...   
140  ['no-code development', 'no-code ai developmen...   
141  ['ai risk management', 'risk management', 'ris...   
142  ['gans (generative adversarial networks)', 'ge...   
143  ['serverless computing', 'serverless ai', 'ser...   

                                       members_cleaned  cleaned_size  \
0    ['audio llms', 'code generation (llms)', 'code...           123   
1    ['alexa', 'alexa integration', 'alexa skill de...           115   
2    ['a2a protocol', 'action', 'action agent', 'ag...           105   
3    ['ai data management', 'data acquisition', 'da...            97   
4    ['1-bit inference', '1-bit llm', '1-bit quanti...            96   
..                                                 ...           ...   
139  ['mcp (model context protocol)', 'mcp (model c...            12   
140  ['design-to-code', 'low-code ai', 'low-code de...            12   
141  ['ai risk assessment', 'ai risk management', '...            11   
142  ['conditiona

In [13]:
# Create enriched skill definitions for embedding generation
# Combines name, description, and representative terms into a structured text

import ast
import json

skills1 = skills.copy()

# Build full_definition with proper formatting and null safety
def build_full_definition(row):
    """Construct a comprehensive skill definition text."""
    parts = []
    
    # Skill name
    if pd.notna(row.get('skill_name')):
        parts.append(f"Name: {row['skill_name']}")
    
    # Description
    if pd.notna(row.get('skill_definition')):
        parts.append(f"Description: {row['skill_definition']}")
    
    # Representative terms/synonyms - parse JSON-like format
    if pd.notna(row.get('closest_5_members')):
        raw_members = row['closest_5_members']
        try:
            # Try to parse as JSON or Python literal (list/array)
            if isinstance(raw_members, str):
                # Remove whitespace and attempt parsing
                raw_members = raw_members.strip()
                if raw_members.startswith('[') and raw_members.endswith(']'):
                    try:
                        members_list = json.loads(raw_members)
                    except json.JSONDecodeError:
                        # Fallback to ast.literal_eval for Python-style lists
                        members_list = ast.literal_eval(raw_members)
                else:
                    members_list = [raw_members]
            elif isinstance(raw_members, (list, tuple)):
                members_list = list(raw_members)
            else:
                members_list = [str(raw_members)]
            
            # Convert list to comma-separated string
            members_str = ', '.join(str(m).strip() for m in members_list if m)
            if members_str:
                parts.append(f"Synonyms/aliases: {members_str}")
        except (ValueError, SyntaxError, TypeError) as e:
            # If parsing fails, use raw value as fallback
            parts.append(f"Synonyms/aliases: {raw_members}")
    
    return "\n".join(parts) if parts else ""

skills1['full_definition'] = skills1.apply(build_full_definition, axis=1)

# Display preview
display_cols = ['cluster_id', 'skill_name', 'full_definition']
available_cols = [c for c in display_cols if c in skills1.columns]
skills1[available_cols].head(10)

cluster_id                              skill_name  \
0           0             LLM Application Engineering   
1           1               Alexa and AWS Development   
2           2                    AI Agent Engineering   
3           6                     AI Data Engineering   
4           7  Model Quantization and Mixed Precision   
5           8                    Speech and Vision AI   
6           9      Reinforcement Learning Engineering   
7          10              AI Accelerator Engineering   
8          11                 AI Security Engineering   
9          12              Autonomous Systems Control   

                                     full_definition  
0  Name: LLM Application Engineering\nDescription...  
1  Name: Alexa and AWS Development\nDescription: ...  
2  Name: AI Agent Engineering\nDescription: Desig...  
3  Name: AI Data Engineering\nDescription: Abilit...  
4  Name: Model Quantization and Mixed Precision\n...  
5  Name: Speech and Vision AI\nDescription: Desig...  
6  Name: Reinforcement Learning Engineering\nDesc...  
7  Name: AI Accelerator Engineering\nDescription:...  
8  Name: AI Security Engineering\nDescription: De...  
9  Name: Autonomous Systems Control\nDescription:...

In [3]:
# === Load Environment Variables ===
load_dotenv()  # Loads variables from .env file into environment

# Retrieve database connection parameters from environment variables
DIAL_API_KEY = os.getenv('DIAL_API_KEY')

#print(DIAL_API_KEY)

In [14]:
# Batch embedding generation for (term + definition) pairs
import json
import math
import time
from datetime import date

# Configuration
EMBED_MODEL = "text-embedding-3-large-1"
AZURE_OPENAI_ENDPOINT = "https://ai-proxy.lab.epam.com"
API_VERSION = "2025-04-01-preview"
BATCH_SIZE = 30
SLEEP_BETWEEN_CALLS = 1.0
OUTPUT_EMB_FILE = f"skill_embedds_{date.today()}.csv"

# Preconditions
required_cols = {"cluster_id","skill_name","skill_definition"}
if not required_cols.issubset(skills.columns):
    raise ValueError(f"'skills' DataFrame missing columns: {required_cols - set(skills.columns)}")

DIAL_API_KEY = os.getenv("DIAL_API_KEY")
if not DIAL_API_KEY:
    raise EnvironmentError("DIAL_API_KEY not found in environment variables.")

# Initialize Azure OpenAI Embedding client
from openai import AzureOpenAI
emb_client = AzureOpenAI(
    api_key=DIAL_API_KEY,
    api_version=API_VERSION,
    azure_endpoint=AZURE_OPENAI_ENDPOINT,
)

# Prepare texts: first line skill name, second line definition
work_df = skills.copy()
work_df["skill_name"] = work_df["skill_name"].astype(str).str.strip()
work_df["skill_definition"] = work_df["skill_definition"].fillna("").astype(str).str.strip()

texts = [f"{t}\n{d}" for t,d in zip(work_df["skill_name"], work_df["skill_definition"])]
print(f"Total texts to embed: {len(texts)}")

embeddings_records = []
num_batches = math.ceil(len(texts)/BATCH_SIZE)
print(f"Processing in {num_batches} batches (size={BATCH_SIZE}) using model '{EMBED_MODEL}'\n")
start_ts = time.time()

for b in range(num_batches):
    start = b*BATCH_SIZE
    end = min((b+1)*BATCH_SIZE, len(texts))
    batch_texts = texts[start:end]
    batch_ids = work_df["cluster_id"].iloc[start:end].tolist()
    batch_terms = work_df["skill_name"].iloc[start:end].tolist()
    batch_defs = work_df["skill_definition"].iloc[start:end].tolist()


    try:
        resp = emb_client.embeddings.create(model=EMBED_MODEL, input=batch_texts)
        # resp.data is a list with .embedding
        if not resp or not hasattr(resp, "data"):
            raise RuntimeError("Unexpected embedding response format")
        vectors = [item.embedding for item in resp.data]
    except Exception as e:
        print(f"\nError embedding batch {b+1}/{num_batches}: {e}")
        vectors = [None]*len(batch_texts)

    for i,(row_id, term, definition, vec) in enumerate(zip(batch_ids, batch_terms, batch_defs, vectors)):
        embeddings_records.append({
            "id": row_id,
            "term": term,
            "definition": definition,
            "embedding": json.dumps(vec) if vec is not None else ""
        })

    # Progress output
    if vectors and vectors[0] is not None:
        dim = len(vectors[0])
    else:
        dim = "?"
    print(f"Batch {b+1}/{num_batches} done: rows {start}-{end-1} | dim={dim}")
    time.sleep(SLEEP_BETWEEN_CALLS)

elapsed = time.time() - start_ts
print(f"\nEmbedding complete in {elapsed:.2f}s")

# Build embeddings DataFrame
emb_df = pd.DataFrame(embeddings_records)
non_empty = (emb_df["embedding"].str.len() > 0).sum()
print(f"Rows embedded (non-empty vectors): {non_empty}/{len(emb_df)}")

# Define output path for embeddings (Clusters folder)
emb_output_path = r"C:\Users\Denis_Davydov2\OneDrive - EPAM\Prophet_AI_docs\Datasets\AI_skills\Clusters"

# Persist to CSV (embedding stored as JSON array string)
emb_df.to_csv(os.path.join(emb_output_path, OUTPUT_EMB_FILE), index=False, encoding="utf-8-sig")
print(f"Saved embeddings to: {os.path.join(emb_output_path, OUTPUT_EMB_FILE)}")

# Preview
emb_df

Total texts to embed: 144
Processing in 5 batches (size=30) using model 'text-embedding-3-large-1'

Batch 1/5 done: rows 0-29 | dim=3072
Batch 1/5 done: rows 0-29 | dim=3072
Batch 2/5 done: rows 30-59 | dim=3072
Batch 2/5 done: rows 30-59 | dim=3072
Batch 3/5 done: rows 60-89 | dim=3072
Batch 3/5 done: rows 60-89 | dim=3072
Batch 4/5 done: rows 90-119 | dim=3072
Batch 4/5 done: rows 90-119 | dim=3072
Batch 5/5 done: rows 120-143 | dim=3072
Batch 5/5 done: rows 120-143 | dim=3072

Embedding complete in 20.14s
Rows embedded (non-empty vectors): 144/144
Saved embeddings to: C:\Users\Denis_Davydov2\OneDrive - EPAM\Prophet_AI_docs\Datasets\AI_skills\Clusters\skill_embedds_2025-11-13.csv

Embedding complete in 20.14s
Rows embedded (non-empty vectors): 144/144
Saved embeddings to: C:\Users\Denis_Davydov2\OneDrive - EPAM\Prophet_AI_docs\Datasets\AI_skills\Clusters\skill_embedds_2025-11-13.csv


id                                    term  \
0      0             LLM Application Engineering   
1      1               Alexa and AWS Development   
2      2                    AI Agent Engineering   
3      6                     AI Data Engineering   
4      7  Model Quantization and Mixed Precision   
..   ...                                     ...   
139  136        MCP Server and Agent Development   
140  135         Low-code No-code AI Development   
141  141                AI Model Risk Management   
142  137        GAN Development and Optimization   
143  138               Serverless AI Engineering   

                                            definition  \
0    Design, build, and deploy LLM-powered applicat...   
1    Design, build, and deploy Alexa skills and voi...   
2    Design, program, and deploy autonomous AI agen...   
3    Ability to design, build, and manage scalable ...   
4    Ability to design, implement, and optimize low...   
..                                                 ...   
139  Build and integrate MCP servers and agents tha...   
140  Build and deploy AI/ML applications and automa...   
141  Ability to assess, quantify, prioritize, and m...   
142  Design, implement, and train GAN variants (cGA...   
143  Design, deploy, and optimize ML and RL workloa...   

                                             embedding  
0    [-0.016113433986902237, 0.011658730916678905, ...  
1    [-0.015863992273807526, 0.007875855080783367, ...  
2    [-0.008975588716566563, -0.03321722149848938, ...  
3    [-0.032141365110874176, 0.004350118804723024, ...  
4    [-0.017981242388486862, 0.0031784838065505028,...  
..                                                 ...  
139  [-0.007689556572586298, -0.0217274222522974, -...  
140  [-0.013128919526934624, -0.021230043843388557,...  
141  [-0.027843959629535675, -0.018969332799315453,...  
142  [-0.008705326355993748, -0.033860329538583755,...  
143  [-0.01654067076742649, -0.02192225493490696, -...  

[144 rows x 4 columns]

Saved embeddings to: C:\Users\Denis_Davydov2\OneDrive - EPAM\Prophet_AI_docs\Datasets\AI_skills\Clusters\skill_embedds_2025-11-13.csv
